<a href="https://colab.research.google.com/github/Eddy109109/senators_bill_recommendation/blob/main/Senators_bill_recommendation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#라이브러리


In [ ]:
###################### 수정 #################################
! pip install konlpy

     |████████████████████████████████| 19.4MB 1.6MB/s 
     |████████████████████████████████| 92kB 8.4MB/s 
     |████████████████████████████████| 460kB 32.4MB/s 
  Found existing installation: beautifulsoup4 4.6.3
    Uninstalling beautifulsoup4-4.6.3:
      Successfully uninstalled beautifulsoup4-4.6.3


In [ ]:
###################### 수정 #################################
!curl -s https://raw.githubusercontent.com/konlpy/konlpy/master/scripts/mecab.sh | bash -x

+ mecab_dicdir=/usr/local/lib/mecab/dic/mecab-ko-dic
+ set -e
++ uname
+ os=Linux
+ [[ ! Linux == \L\i\n\u\x ]]
+ hash sudo
+ sudo=sudo
+ python=python3
+ hash pyenv
+ at_user_site=
++ check_python_site_location_is_writable
++ python3 -
+ [[ 1 == \0 ]]
+ hash automake
+ echo 'Installing automake (A dependency for mecab-ko)'
Installing automake (A dependency for mecab-ko)
+ install_automake
+ '[' Linux == Linux ']'
++ grep -Ei 'debian|buntu|mint' /etc/lsb-release /etc/os-release
+ '[' '/etc/lsb-release:DISTRIB_ID=Ubuntu
/etc/lsb-release:DISTRIB_DESCRIPTION="Ubuntu 18.04.5 LTS"
/etc/os-release:NAME="Ubuntu"
/etc/os-release:ID=ubuntu
/etc/os-release:ID_LIKE=debian
/etc/os-release:PRETTY_NAME="Ubuntu 18.04.5 LTS"
/etc/os-release:HOME_URL="https://www.ubuntu.com/"
/etc/os-release:SUPPORT_URL="https://help.ubuntu.com/"
/etc/os-release:BUG_REPORT_URL="https://bugs.launchpad.net/ubuntu/"
/etc/os-release:PRIVACY_POLICY_URL="https://www.ubuntu.com/legal/terms-and-policies/privacy-policy"
/etc/os

In [ ]:
# !set -x \
# && pip install konlpy \
# && curl -s https://raw.githubusercontent.com/konlpy/konlpy/master/scripts/mecab.sh | bash -x

In [ ]:
!git clone https://github.com/facebookresearch/fastText.git
!cd fastText
!pip install fastText
import fasttext.util

Cloning into 'fastText'...
remote: Enumerating objects: 3854, done.
remote: Total 3854 (delta 0), reused 0 (delta 0), pack-reused 3854
Receiving objects: 100% (3854/3854), 8.22 MiB | 23.66 MiB/s, done.
Resolving deltas: 100% (2417/2417), done.
     |████████████████████████████████| 71kB 3.5MB/s 
  Created wheel for fastText: filename=fasttext-0.9.2-cp37-cp37m-linux_x86_64.whl size=3096985 sha256=04b1712572801545c6db4ab028d9457058b52538e3352b7cd79c9cf5ccddc01f
  Stored in directory: /root/.cache/pip/wheels/98/ba/7f/b154944a1cf5a8cee91c154b75231136cc3a3321ab0e30f592
Successfully built fastText


In [ ]:
!pip install selenium

     |████████████████████████████████| 911kB 5.2MB/s 


In [ ]:
import re
import json
import time
import konlpy
import gensim 
import glob, os
import requests
import fasttext
import numpy as np
import pandas as pd
import seaborn as sns
from glob import glob
import urllib.request
import matplotlib as mpl
from matplotlib import rc

from bs4 import BeautifulSoup
from tqdm.notebook import tqdm
from collections import Counter
import matplotlib.pyplot as plt
from PIL import Image, ImageFilter
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
import matplotlib.font_manager as fm
from matplotlib import font_manager, rc
from wordcloud import ImageColorGenerator
from IPython.display import Image, display
from sklearn.metrics import silhouette_score
from selenium.webdriver.common.keys import Keys
from gensim.models import Word2Vec, FastText, Doc2Vec
from sklearn.metrics.pairwise import cosine_similarity
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import HoverTool, ColumnDataSource, value
from sklearn.feature_extraction.text import TfidfVectorizer
from wordcloud import WordCloud, STOPWORDS as stopwords
from selenium.webdriver.common.action_chains import ActionChains
%matplotlib inline
rc('font', family='AppleGothic')
plt.rcParams['axes.unicode_minus'] = False
pd.set_option("display.max_columns", 100)
pd.set_option("display.max_rows", 100)

In [ ]:
from konlpy.tag import Mecab

In [ ]:
mecab = Mecab()

In [ ]:
mecab.morphs("아버지 방으로 들어 가신다")

['아버지', '방', '으로', '들', '어', '가', '신다']

#함수모음


In [ ]:
mecab = Mecab()

def tokenized_mecab(data):
    result = mecab.morphs(data)
    result = ' '.join(result)
    return result

In [ ]:
tokenized_mecab("아버지 방으로 들어 가신다")

'아버지 방 으로 들 어 가 신다'

In [ ]:
#stopwords에 해당 안되는 token값 찾기
def out_stopwords(data, list_stopwords):
    data = data.split(" ")
    print("data = ", data)
    list_stopwords = list_stopwords
    result = [token for token in data if token not in list_stopwords]
    print("result=", result)
    print("="*100)
    return result

In [ ]:
def show_bills(bills_id, df_bills):
    for bill_id in bills_id:
        print(df_bills[df_bills['bill_id']==int(bill_id)]['법안명_법안내용'].iloc[0])
        print("*"*80)        
        
def input2vec(user_input, stopword_list, word2vec_word_dict):
    tokenized_input = tokenized_mecab(user_input)
    tokenized_input_outStopwords = out_stopwords(tokenized_input, stopword_list)
    
    list_vector = []
    for word in tokenized_input_outStopwords:
        if word in word_dict.keys():
            list_vector.append(word_dict[word])
    user_vector = (np.sum(list_vector, axis=0) / len(list_vector)).tolist()
    return user_vector

def similar_senators(user_vector, df_snt):
    similarity = {}
    for idx in df_snt.index:
        if df_snt.loc[idx]['vector'] != '0.0':
            sim = cosine_similarity(np.array(user_vector).reshape(1,-1), np.array([float(i) for i in df_snt.loc[idx]['vector'][1:-1].split(', ')]).reshape(1,-1))
        similarity[str(df_snt.loc[idx]['id'])] = float(sim)
    similarity = {key: value for key, value in sorted(similarity.items(), key=lambda item: item[1], reverse=True)}
    rating = [key for key, value in sorted(similarity.items(), key=lambda item: item[1], reverse=True)]
    top_5 = rating[:5]
    result = {}
    for i in top_5:
        result[i] = str(abs(round((similarity[i]*100), 2))) + "%"
        
    return result

def similar_bills(user_vector, df_bills, df_snt, fasttext_word_dict, snt_ids):
    senators = {}
    for id_ in tqdm(snt_ids):
        id_ = int(id_)
        NAME_HAN = df_snt[df_snt['id']==id_]['NAME_HAN'].iloc[0]
        bills_snt_ids = df_bills[df_bills['senators_list'].str.contains(NAME_HAN)]['BILL_ID'].values
        
        similarity = {}
        for bill_id in bills_snt_ids:
            sim = cosine_similarity(np.array(user_vector).reshape(1,-1), np.array([float(i) for i in df_bills[df_bills['BILL_ID']==bill_id].iloc[0]['vector'][1:-1].split(', ')]).reshape(1,-1))
            similarity[df_bills[df_bills['BILL_ID']==bill_id]['BILL_ID'].iloc[0]] = float(sim)
        similarity = {key: value for key, value in sorted(similarity.items(), key=lambda item: item[1], reverse=True)}
        rating = [str(key) for key, value in sorted(similarity.items(), key=lambda item: item[1], reverse=True)]
        top_5 = rating[:3]
        result = {}
        for i in top_5:
            result[i] = str(abs(round((similarity[i]*100), 2))) + "%"
        senators[id_] = result
    
    return senators

def show_bills(senators_id_bills, df_bills, df_snt):
    result = []
    
    for snt_id in senators_id_bills:
        name = df_snt[df_snt['id'] == snt_id]['NAME'].iloc[0]
        for bill_id in list(senators_id_bills[snt_id]):
            dict_temp = {}
            dict_temp['발의자'] = name
            dict_temp['법안명'] = df_bills[df_bills['BILL_ID']==bill_id]['BILL_NAME'].iloc[0]
            dict_temp['법안내용'] = df_bills[df_bills['BILL_ID']==bill_id]['bill_content'].iloc[0]
            result.append(dict_temp)
    return result

def show_results(df_results, dict_images):
    for snt in df_results['발의자'].unique():
        display(Image('./images/'+snt+'.jpg'))
        print("{} 의원".format(snt))
        df_temp = df_results[df_results['발의자']==snt]
        for idx in df_temp.index:
            print("*"*30, df_temp.loc[idx]['법안명'], "*"*30)
            print(df_temp.loc[idx]['법안내용'], '\n')

# 정보 크롤링

In [ ]:
#CSV data를 하나의 딕셔너리 형태로 변환

dict_data = {}
for i in glob('/content/data/*.csv'):
    try:
        dict_data[i.split('/')[3].split('.csv')[0]] = pd.read_csv(i)
    except:
        dict_data[i.split('/')[3].split('.csv')[0]] = pd.read_csv(i, encoding='cp949')

/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (2,5,17) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [ ]:
dict_data

{'new_people':       DAESU                                                DAE DAE_NM NAME  \
 0        21  제19대국회의원(경남 창원시성산구) 정당_66\r\n제21대국회의원(경남 창원시성산...  21대의원  강기윤   
 1        21                              제21대국회의원(대구동구을) 정당_74  21대의원  강대식   
 2        21                            제21대국회의원(경기안양시만안구) 정당_7  21대의원  강득구   
 3        21                             제21대국회의원(경남진주시을) 정당_74  21대의원  강민국   
 4        21                               제21대국회의원(비례대표) 정당_30  21대의원  강민정   
 ...     ...                                                ...    ...  ...   
 5600      1                                 제헌국회의원(김제을)조선민족청년단   제헌의원  홍희종   
 5601      1                               제헌국회의원(순천갑)대한촉성농민총연맹   제헌의원  황두연   
 5602      1                 제헌국회의원(여수을)무소속\r\n제2대국회의원(여천)대한국민당   제헌의원  황병규   
 5603      1                                      제헌국회의원(진양)무소속   제헌의원  황윤호   
 5604      1  제헌국회의원(평창)대한독립촉성국민회\r\n제4대국회의원(평창)무소속\r\n제6대국회...   제헌의원  황호현   
 
      NAME_HAN   JA   HO          BI

##-1 사진


In [ ]:
#
def download(URL, short_name):
    list_temp = []
    short_name = short_name[0].text.split(' ',1)[-1]
    if short_name not in list_temp:
        list_temp.append(short_name)
        fullName = "/content/images/" + short_name + ".jpg"
        urllib.request.urlretrieve(URL, fullName)   
    else:
        fullName = "/content/images/" + short_name + " (2).jpg"
        urllib.request.urlretrieve(URL, fullName)   

In [ ]:
import selenium
from selenium import webdriver
from selenium.webdriver import ActionChains

from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By

from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import Select
from selenium.webdriver.support.ui import WebDriverWait

In [ ]:
#크롬에서 크롤링 하기위해 별도설치 chromedriver, webdriver
!apt-get update # to update ubuntu to correctly run apt install

!apt install chromium-chromedriver

Hit:1 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease
Ign:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:4 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:5 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease
Hit:6 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Hit:7 http://security.ubuntu.com/ubuntu bionic-security InRelease
Hit:8 http://archive.ubuntu.com/ubuntu bionic InRelease
Hit:9 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Hit:10 http://archive.ubuntu.com/ubuntu bionic-updates InRelease
Hit:12 http://archive.ubuntu.com/ubuntu bionic-backports InRelease
Hit:13 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu bionic InRelease
Hit:14 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic 

In [ ]:
#크롬1
from selenium import webdriver
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless') #내부 창을 띄울 수 없으므로 설정
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')
wd = webdriver.Chrome('chromedriver',chrome_options=chrome_options)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:7: DeprecationWarning: use options instead of chrome_options
  import sys


In [ ]:
#크롬2
!cp /usr/lib/chromium-browser/chromedriver /usr/bin
import sys
sys.path.insert(0,'/usr/lib/chromium-browser/chromedriver')
from selenium import webdriver
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless')
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')
wd = webdriver.Chrome('chromedriver',chrome_options=chrome_options)

cp: '/usr/lib/chromium-browser/chromedriver' and '/usr/bin/chromedriver' are the same file


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: DeprecationWarning: use options instead of chrome_options
  # Remove the CWD from sys.path while we load stuff.


In [ ]:
driver = webdriver.Chrome('chromedriver',chrome_options=chrome_options)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: DeprecationWarning: use options instead of chrome_options
  """Entry point for launching an IPython kernel.


In [ ]:
# 열러라 국회 의원 접속
driver.get('http://watch.peoplepower21.org/?act=&mid=AssemblyMembers&vid=&mode=search&name=&party=&region=&sangim=&gender=&age=&elect_num=')

In [ ]:
start_time = time.time()

for page in range(1,11):
    if page != 1:
        driver.get('http://watch.peoplepower21.org/?mid=AssemblyMembers&mode=search&party=&region=&sangim=&gender=&elect_num=&page=' + str(page))
    for person in range(2,32):
        short_name = driver.find_elements_by_css_selector('#content > div.col-md-8 > div:nth-child('+ str(person)+')> div > a:nth-child(2) > h4')
        image = driver.find_elements_by_tag_name('#content > div.col-md-8 > div:nth-child(' + str(person)+ ') > div > a:nth-child(1) > img')
        src = image[0].get_attribute('src')
        download(src, short_name)
print("---{}초 걸렸슴둥---".format(time.time()-start_time))

---253.45023322105408초 걸렸슴둥---


##-2 법안내용

In [ ]:
dict_data

{'new_people':       DAESU                                                DAE DAE_NM NAME  \
 0        21  제19대국회의원(경남 창원시성산구) 정당_66\r\n제21대국회의원(경남 창원시성산...  21대의원  강기윤   
 1        21                              제21대국회의원(대구동구을) 정당_74  21대의원  강대식   
 2        21                            제21대국회의원(경기안양시만안구) 정당_7  21대의원  강득구   
 3        21                             제21대국회의원(경남진주시을) 정당_74  21대의원  강민국   
 4        21                               제21대국회의원(비례대표) 정당_30  21대의원  강민정   
 ...     ...                                                ...    ...  ...   
 5600      1                                 제헌국회의원(김제을)조선민족청년단   제헌의원  홍희종   
 5601      1                               제헌국회의원(순천갑)대한촉성농민총연맹   제헌의원  황두연   
 5602      1                 제헌국회의원(여수을)무소속\r\n제2대국회의원(여천)대한국민당   제헌의원  황병규   
 5603      1                                      제헌국회의원(진양)무소속   제헌의원  황윤호   
 5604      1  제헌국회의원(평창)대한독립촉성국민회\r\n제4대국회의원(평창)무소속\r\n제6대국회...   제헌의원  황호현   
 
      NAME_HAN   JA   HO          BI

In [ ]:
sug = dict_data['suggest']

In [ ]:
dict_data['suggest'].columns

Index(['BILL_ID', 'BILL_NO', 'BILL_NAME', 'COMMITTEE', 'PROPOSE_DT',
       'PROC_RESULT', 'AGE', 'DETAIL_LINK', 'PROPOSER', 'MEMBER_LIST',
       'RST_PROPOSER', 'PUBL_PROPOSER'],
      dtype='object')

In [ ]:
dict_data.keys()

dict_keys(['suggest', 'process', 'new_people'])

In [ ]:
dict_data["process"].head(1)

AGE ANNOUNCE_DT BDG_PRESENT_DT BDG_PROC_DT BDG_SUBMIT_DT  \
0   21         NaN            NaN         NaN           NaN   

                              BILL_ID BILL_KIND  \
0  PRC_A2Q0T0X9B2P4F0M9N3P8K5S9I7K5N9        기타   

                                   BILL_NAME  BILL_NO  BLANK_TCNT  \
0  본회의 의결을 요하는 국정감사대상기관 승인의 건(과학기술정보방송통신위원장)  2104197         NaN   

    COMMITTEE_NM COMMITTEE_PRESENT_DT COMMITTEE_PROC_DT COMMITTEE_SUBMIT_DT  \
0  과학기술정보방송통신위원회                  NaN               NaN                 NaN   

  CURR_TRANS_DT LAW_PRESENT_DT LAW_PROC_DT LAW_SUBMIT_DT  \
0           NaN            NaN         NaN           NaN   

                                            LINK_URL  NO_TCNT PROC_RESULT_CD  \
0  https://likms.assembly.go.kr/bill/billDetail.d...      NaN           원안가결   

        PROPOSER PROPOSER_KIND_CD  PROPOSE_DT RGS_PRESENT_DT RGS_PROC_DT  \
0  과학기술정보방송통신위원장              위원장  2020-09-24     2020-09-24  2020-09-24   

   VOTE_TCNT  YES_TCNT  
0        NaN       NaN

In [ ]:
###################### 추가 #################################
#법안이 많아서 0.1% 샘플 추출해서 진행
sug = sug.sample(frac=0.001)

In [ ]:
sug

BILL_ID  BILL_NO  \
40524  PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3  1900574   
58189                              026103   162692   
54484                              036814   174918   
53528  PRC_V0Y7Z0N4I1H0O0J9S4C6C3Q5B3U3F7   176375   
54974                              034791   174238   
47105  PRC_T0T9Q1W1D1K0P0D9D4Y9B4F9J5Y2P3  1806499   
41606  PRC_V1P1D1L1K1F0Y1D9I1A0R5A0M8Q2C5  1813836   
48385  PRC_K0A9G0Y5F2I2V1X5T0I0O2H9E9I1E0  1804919   
28668  PRC_G1O5G0D4D1A5C1Z4P5V5P3L5R2P2U8  1914717   
62514                              000772    20231   
51748  PRC_O0R8T0N8K1V1I1F0H1C9R4M1W1F9T5  1800580   
38636  PRC_P1P2F1O1Q2A9H1H5F2M4H3B8U1U9Y1  1902854   
13995  PRC_S1V8O0E4Q3U0M1S7J2S1U0V6Q8I2X7  2013331   
50051  PRC_N0D8D1G2C0V2V1M0Z3J0Z5Z8T4U9Y0  1802800   
24574  PRC_C1U6W0P7C2S6K1W5K2J1S5K6S3A1X7  2001202   
4054   PRC_U2S0T0Y4K0E9J1D5Q5V3T5Y0T4F8G6  2024837   
21788  PRC_F1F6Z1B2E1U3Y1Y3L1F6J4W8R5G4Q9  2004334   
57720                              028458   170382   
20154  PRC_Q1X7D0S3I1J7S1K4T3U2U3Q8T8J9B3  2006252   
4712   PRC_P1Y9W1L1D1K4H1F4E5S1V2P7W8D9R8  2023793   
53892  PRC_W0B7J0X1S0D5M1P5Q1R0V3Y6C8V9A5   175913   
31300  PRC_E1K4I0P8P2L1L1F8B1Z8R5M4A5P6W3  1911445   
46904  PRC_R0C9U1S1J2D7G1V0W2J9F4J0F0T5D5  1806735   
48587  PRC_Q0W9U0W4I2X2L1A0I3Z7C3V9I8S3N6  1804647   
33468  PRC_W1Z3U1N2Z2R7I1R4B2W6P2V0Y6C4G7  1908811   
19656  PRC_C1T7J0K4G2J0X1L3A5H7J4A7K2I2U0  2006798   
8361   PRC_Q1K9W0S4P1H1Q1N7T1W6Q5O7U1K6H8  2019755   
59339                              016784   160669   
57469                              029079   170787   
14362  PRC_W1Y8H0O4H0U6G1X8U4O0S0E0T1Y6A3  2012957   
57021                              030171   171479   
27545  PRC_G1D5L0N7I1R4Q1I1L2A1B4P0G2O0C6  1916066   
40488  PRC_L1Z2U0B7U1W1B1G3U5Z8C1D9L6N9Q8  1900623   
9882   PRC_A1E9F0W1Z0A7A1C6W3N8U1V3Y9B7Z4  2018073   
35575  PRC_V1X3V0X8J1H4Z1R1V4T1C2J1N0Q2N8  1906373   
53935  PRC_N0J6H1U2O2N9D1A0G1R3B2F1D2W3X7   175853   
29565  PRC_I1R5U0S1J1T9Z1H3A0E6K4O7I9Y3K1  1913729   
20931  PRC_A1Y7X0B2E0L1P1Z0N5S5O3W9V5H2Q9  2005355   
20665  PRC_N1Q7W0O2D1V4C1F8Q4N4W1P5I8I3B7  2005633   
46672  PRC_L0L9P1T2Z2B1O1M8Y2A8C3R2V7H6Z7  1807063   
4941   PRC_I1H9C1V1W0S4Z1X0W2Z7V3L1D8B1C8  2023556   
58912                              017547   161433   
14978  PRC_F1O8E0T2H2D8B1Z8E1S5O1P1O3F0D3  2012248   
44292  PRC_O1Y0L1M2W1O0W1Q1N3Q1P0S0A4T2E2  1810290   
10514  PRC_G1V8V1W2P1O0B1Y0N5G7M5Y1J5M7X5  2017328   
3156   PRC_R2H0I0G6R2B4B0S9X3P6F5F1W5D8N5  2100914   
15016  PRC_P1L8A0V2E2L7M1M7V5G1N5N0G2T3O6  2012173   
21695  PRC_J1M6K1Z2O1A6F1X6C3X0J0O9B4Q0Q4  2004430   
13418  PRC_Q1D8Z0T6W2U1A1E4L1T1X4G4X2V3B8  2013968   
33287  PRC_S1B4Q0F1J1R7H1J6M2M8R3Q3Y0P1W8  1909095   
46091  PRC_D1H0A0Z3S2X3T1A7P0K2N4U0G4J5U3  1807945   
50636  PRC_E0O8C1X1D1F4L1S7P4F1O4C2V3Q1Y9  1802051   
27584  PRC_I1E5U0B7F0J8E1M4O4R0Z5C4Q1V0S4  1916015   
33269  PRC_J1W4W0X1I2I1K1B0F4C7B4N5H1T2E5  1909114   
10487  PRC_P1Q8Z1S2K1H0H1W3X4G8B5Y5P3A0O4  2017355   
15868  PRC_F1X7W1W2F2O9M1F7J5S1B0U5J3S6J6  2011165   
25098  PRC_V1Q6D0I7F0F1G1E4D2E6U2M8J7J7I9  2000627   
57683                              028525   170428   
49499  PRC_H0O9C0Z1H1H4N1A0O2R2P1F8D3Z4H3  1803543   
30253  PRC_M1W4I1H1M2B6E1U7Y2I9X5Z0H7H0D6  1912681   
7400   PRC_I1Q9T0N5L3F1C1G8E1R6B0O8P8X5D8  2020769   
25536  PRC_Q1J6K0X6H0S2I1Z3G1R7Y2C4V6X7Q0  2000077   
11827  PRC_S1E8O0X9Y2L8S1Z7E1N2L5I0T3V7Z3  2015785   

                               BILL_NAME        COMMITTEE  PROPOSE_DT  \
40524     산업기술의 유출방지 및 보호에 관한 법률 일부개정법률안        산업통상자원위원회  2012-07-09   
58189                          주세법중개정법률안          재정경제위원회  2003-09-30   
54484                       하수도법 일부개정법률안          환경노동위원회  2006-09-14   
53528           농업협동조합의구조개선에관한법률 일부개정법률안        농림해양수산위원회  2007-04-06   
54974         맹견의 사육·관리 및 수입제한 등에 관한 법률안        농림해양수산위원회  2006-04-12   
47105                   가축전염병예방법 일부개정법률안        농림수산식품위원회  2009-11-10   
41606              중소기업진흥에 관한 법률 일부개정법률안          지식경제위원회  2011-11

In [ ]:
dict_crawl_data = {}
for idx in tqdm(sug.index):
    bill_id = sug.loc[idx]['BILL_ID']
    print("bill_id =", bill_id)
    url = sug.loc[idx]['DETAIL_LINK']
    print("url = ", url)
    res = requests.get(url)

    soup = BeautifulSoup(res.text, 'html.parser')
    container = soup.select('#summaryContentDiv')
    if len(container) == 0:
        dict_crawl_data[bill_id] = '내용없음'
    else:
        contents = container[0].text.strip()
        ###################### 추가 #################################
        if len(contents)==0:
          dict_crawl_data[bill_id] = "내용없음"
        else :    
          dict_crawl_data[bill_id] = contents

bill_id = PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3&ageFrom=19&ageTo=19
bill_id = 026103
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=026103&ageFrom=16&ageTo=16
bill_id = 036814
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=036814&ageFrom=17&ageTo=17
bill_id = PRC_V0Y7Z0N4I1H0O0J9S4C6C3Q5B3U3F7
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=PRC_V0Y7Z0N4I1H0O0J9S4C6C3Q5B3U3F7&ageFrom=17&ageTo=17
bill_id = 034791
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=034791&ageFrom=17&ageTo=17
bill_id = PRC_T0T9Q1W1D1K0P0D9D4Y9B4F9J5Y2P3
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=PRC_T0T9Q1W1D1K0P0D9D4Y9B4F9J5Y2P3&ageFrom=18&ageTo=18
bill_id = PRC_V1P1D1L1K1F0Y1D9I1A0R5A0M8Q2C5
url =  http://likms.assembly.go.kr/bill/billDetail.do?billId=PRC_V1P1D1L1K1F0Y1D9I1A0R5A0M8Q2C5&ageFrom=18&ageTo=18
bill_id = PRC_K0A9G0Y5F2I2V1X5T0I0O2H9E9I

In [ ]:
sug.head()

BILL_ID  BILL_NO  \
40524  PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3  1900574   
58189                              026103   162692   
54484                              036814   174918   
53528  PRC_V0Y7Z0N4I1H0O0J9S4C6C3Q5B3U3F7   176375   
54974                              034791   174238   

                            BILL_NAME  COMMITTEE  PROPOSE_DT PROC_RESULT  AGE  \
40524  산업기술의 유출방지 및 보호에 관한 법률 일부개정법률안  산업통상자원위원회  2012-07-09          폐기   19   
58189                       주세법중개정법률안    재정경제위원회  2003-09-30          폐기   16   
54484                    하수도법 일부개정법률안    환경노동위원회  2006-09-14          폐기   17   
53528        농업협동조합의구조개선에관한법률 일부개정법률안  농림해양수산위원회  2007-04-06      대안반영폐기   17   
54974      맹견의 사육·관리 및 수입제한 등에 관한 법률안  농림해양수산위원회  2006-04-12      임기만료폐기   17   

                                             DETAIL_LINK     PROPOSER  \
40524  http://likms.assembly.go.kr/bill/billDetail.do...  정희수의원 등 12인   
58189  http://likms.assembly.go.kr/bill/billDetail.do...   김정부의원등 17인   
54484  http://likms.assembly.go.kr/bill/billDetail.do...   박재완의원등 11인   
53528  http://likms.assembly.go.kr/bill/billDetail.do...   김명주의원등 10인   
54974  http://likms.assembly.go.kr/bill/billDetail.do...   이성권의원등 10인   

                                             MEMBER_LIST RST_PROPOSER  \
40524  http://likms.assembly.go.kr/bill/coactorListPo...          정희수   
58189  http://likms.assembly.go.kr/bill/coactorListPo...          김정부   
54484  http://likms.assembly.go.kr/bill/coactorListPo...          박재완   
53528  http://likms.assembly.go.kr/bill/coactorListPo...          김명주   
54974  http://likms.assembly.go.kr/bill/coactorListPo...          이성권   

                                           PUBL_PROPOSER  
40524        고희선,권은희,박대동,박인숙,이만우,이명수,이현재,정우택,주영순,주호영,황영철  
58189  강신성일,강인섭,권오을,김광원,박근혜,박상규,송광호,윤영탁,윤한도,이경재,이상배,임...  
54484            공성진,김애실,배일도,신상진,심재철,엄호성,윤건영,이경재,이성구,이주호  
53528                공성진,남경필,맹형규,신중식,원희룡,이명규,이성권,이인기,최구식  
54974                권철현,김명주,김석준,김양수,김희정,박형준,서상기,이계경,정진석

In [ ]:
sug['BILL_ID'].map(dict_crawl_data)

40524    제안이유 및 주요내용\n\n  산업기밀보호센터에 따르면, 2005년 ～ 2011년간...
58189    ■ 제안이유\n  주류에 대한 주세 부과의 목적은 크게 재정수입 확보와 과도한 음주...
54484    ■ 제안이유 및 주요내용\n그동안 사실상 세금과 다름없이 강제 징수되어 국민들로부터...
53528    ■ 제안이유 \n시중 금융기관의 구조개선과는 달리, 농업협동조합중앙회는「농업협동조합...
54974    ■ 제안이유\n최근 도사견 등 맹견에 의한 인명피해가 빈번히 발생하여 심각한 사회문...
47105    제안이유 및 주요내용\n  현행법은 가축전염병에 걸렸거나 걸렸다고 믿을 만한 역학조...
41606    제안이유 및 주요내용\n  현행법은 중소기업진흥공단의 사업을 위하여 적립된 기금의 ...
48385    제안이유\n  현재 의료사고로 인한 피해를 구제받기 위해서는 「의료법」에 따라 설치...
28668    제안이유 및 주요내용\n\n  유치원이나 어린이집, 체육시설, 학원 등의 어린이통학...
62514    ■ 제안이유\n\n現行法은 알미늄과 食器, 법랑製品은 無稅임에도 不拘하고 一般大衆用...
51748    제안이유\n  롯데호텔 제주, 롯데쇼핑, 농심 메가마트, 교보생명, 대한생명, 두산...
38636    제안이유 및 주요내용\n\n  현행법상 교역 및 경제 분야 협력사업 추진 중 대통령...
13995    제안이유 및 주요내용\n\n  여권에는 「여권법」에 따라 성명, 성별, 주민등록번호...
50051    제안이유 및 주요내용\n  현행법은 안전인증 및 자율안전확인신고 등의 표시가 없는 ...
24574    ■ 제안이유 및 주요내용 \n\n  현행법 제16조의3에서 규정하고 있는 6？25전...
4054     제안이유\n\n  여야가 적대적 대립 속에 국회파행으로 이어지는 악순환은 지난 20...
21788    ■ 제안이유 및 주요내용 \n\n\n제안이유\n\n  현행법은 민간시장을 통한 일명.

In [ ]:
sug['bill_content'] = sug['BILL_ID'].map(dict_crawl_data)

In [ ]:
####### 추가 ##########################################################3
dict_crawl_data = {}
for idx in tqdm(sug.index):
  bill_id = sug.loc[idx]['BILL_ID']
  print("bill_id =", bill_id)
  url = sug.loc[idx]['MEMBER_LIST']
  print("url = ", url)
  res = requests.get(url)

  soup = BeautifulSoup(res.text, 'html.parser')
  container = soup.select('.mt20 a')
  print("container = ", container)
  if len(container) == 0:
    dict_crawl_data[bill_id] = "발의자 없음"
  else:

    if len(container)==0:
      dict_crawl_data[bill_id] = "발의자 없음"
    else :
      member_list=[] 
      for a in container:
        print("a.text = ", a.text)
        member_list.append(a.text) 
      
      print("member_list =", member_list)
      dict_crawl_data[bill_id] = " ".join(member_list)
        
  print("="*100)

bill_id = PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3
url =  http://likms.assembly.go.kr/bill/coactorListPopup.do?billId=PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3
container =  [<a>정희수(새누리당/鄭熙秀)</a>, <a>고희선(새누리당/高羲善)</a>, <a>권은희(새누리당/權恩嬉)</a>, <a>박대동(새누리당/朴大東)</a>, <a>박인숙(새누리당/朴仁淑)</a>, <a>이만우(새누리당/李萬雨)</a>, <a href="http://www.assembly.go.kr/assm/memPop/memPopup.do?dept_cd=9770602" target="_blank">이명수(자유선진당/李明洙)</a>, <a>이현재(새누리당/李賢在)</a>, <a>정우택(새누리당/鄭宇澤)</a>, <a>주영순(새누리당/朱永順)</a>, <a href="http://www.assembly.go.kr/assm/memPop/memPopup.do?dept_cd=9770883" target="_blank">주호영(새누리당/朱豪英)</a>, <a>황영철(새누리당/黃永哲)</a>]
a.text =  정희수(새누리당/鄭熙秀)
a.text =  고희선(새누리당/高羲善)
a.text =  권은희(새누리당/權恩嬉)
a.text =  박대동(새누리당/朴大東)
a.text =  박인숙(새누리당/朴仁淑)
a.text =  이만우(새누리당/李萬雨)
a.text =  이명수(자유선진당/李明洙)
a.text =  이현재(새누리당/李賢在)
a.text =  정우택(새누리당/鄭宇澤)
a.text =  주영순(새누리당/朱永順)
a.text =  주호영(새누리당/朱豪英)
a.text =  황영철(새누리당/黃永哲)
member_list = ['정희수(새누리당/鄭熙秀)', '고희선(새누리당/高羲善)', '권은희(새누리당/權恩嬉)', '박대동(새누리당/朴大東)', '박인숙(새누리당/朴仁淑)', '이만우(새누

In [ ]:
sug['senators_list'] = sug['BILL_ID'].map(dict_crawl_data)

In [ ]:
sug['BILL_ID'].map(dict_crawl_data)

40524    정희수(새누리당/鄭熙秀) 고희선(새누리당/高羲善) 권은희(새누리당/權恩嬉) 박대동(...
58189    김정부 강신성일 강인섭 권오을 김광원 박근혜 박상규 송광호 윤영탁 윤한도 이경재 이...
54484          박재완 공성진 김애실 배일도 신상진 심재철 엄호성 윤건영 이경재 이성구 이주호
53528              김명주 공성진 남경필 맹형규 신중식 원희룡 이명규 이성권 이인기 최구식
54974              이성권 권철현 김명주 김석준 김양수 김희정 박형준 서상기 이계경 정진석
47105           이춘석 박영선 박은수 박준선 신건 양승조 우윤근 유성엽 정동영 주승용 최철국
41606      장병완 강기정 강창일 김재윤 박주선 양승조 유선호 이종걸 전병헌 전혜숙 조정식 최종원
48385      최영희 김상희 박은수 백원우 변재일 안민석 양승조 이미경 이용섭 전혜숙 최규식 최재성
28668    민홍철(새정치민주연합/閔洪喆) 박주선(새정치민주연합/朴柱宣) 부좌현(새정치민주연합/...
62514                                                   류홍
51748    강창일 강기정 김우남 김재윤 김종률 김희철 박기춘 박선숙 송민순 우윤근 이윤석 이진...
38636    심재권(민주당/沈載權) 강창일(민주당/姜昌一) 김성곤(민주당/金星坤) 김윤덕(민주당...
13995    심재권(더불어민주당/沈載權) 강병원(더불어민주당/姜炳遠) 강창일(더불어민주당/姜昌一...
50051          최구식 구본철 권경석 나경원 성윤환 안형환 유승민 이한성 임동규 정갑윤 진성호
24574    민홍철(더불어민주당/閔洪喆) 문희상(더불어민주당/文喜相) 설훈(더불어민주당/薛勳) ...
4054     정병국(미래통합당/鄭柄國) 강창일(더불어민주당/姜昌一) 김경협(더불어민주당/金炅俠)...
21788    윤관석(더불어민주당/尹官石) 기동민(더불어민주당/奇東旻) 김민기(더불어민주당/金敏基.

In [ ]:
####### test
dict_crawl_data = {}
for idx in tqdm(sug.index):
  bill_id = sug.loc[idx]['BILL_ID']
  print("bill_id =", bill_id)
  url = sug.loc[idx]['MEMBER_LIST']
  print("url = ", url)
  res = requests.get(url)

  soup = BeautifulSoup(res.text, 'html.parser')
  container = soup.select('.mt20 a')
  print("container = ", container)
  if len(container) == 0:
    dict_crawl_data[bill_id] = "발의자 없음"
  else:

    if len(container)==0:
      dict_crawl_data[bill_id] = "발의자 없음"
    else :
      member_list=[] 
      for a in container:
        print("a.text = ", a.text)
        member_list.append(a.text) 
      
      print("member_list =", member_list)
      dict_crawl_data[bill_id] = " ".join(member_list)
        
  print("="*100)

bill_id = PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3
url =  http://likms.assembly.go.kr/bill/coactorListPopup.do?billId=PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3
container =  [<a>정희수(새누리당/鄭熙秀)</a>, <a>고희선(새누리당/高羲善)</a>, <a>권은희(새누리당/權恩嬉)</a>, <a>박대동(새누리당/朴大東)</a>, <a>박인숙(새누리당/朴仁淑)</a>, <a>이만우(새누리당/李萬雨)</a>, <a href="http://www.assembly.go.kr/assm/memPop/memPopup.do?dept_cd=9770602" target="_blank">이명수(자유선진당/李明洙)</a>, <a>이현재(새누리당/李賢在)</a>, <a>정우택(새누리당/鄭宇澤)</a>, <a>주영순(새누리당/朱永順)</a>, <a href="http://www.assembly.go.kr/assm/memPop/memPopup.do?dept_cd=9770883" target="_blank">주호영(새누리당/朱豪英)</a>, <a>황영철(새누리당/黃永哲)</a>]
a.text =  정희수(새누리당/鄭熙秀)
a.text =  고희선(새누리당/高羲善)
a.text =  권은희(새누리당/權恩嬉)
a.text =  박대동(새누리당/朴大東)
a.text =  박인숙(새누리당/朴仁淑)
a.text =  이만우(새누리당/李萬雨)
a.text =  이명수(자유선진당/李明洙)
a.text =  이현재(새누리당/李賢在)
a.text =  정우택(새누리당/鄭宇澤)
a.text =  주영순(새누리당/朱永順)
a.text =  주호영(새누리당/朱豪英)
a.text =  황영철(새누리당/黃永哲)
member_list = ['정희수(새누리당/鄭熙秀)', '고희선(새누리당/高羲善)', '권은희(새누리당/權恩嬉)', '박대동(새누리당/朴大東)', '박인숙(새누리당/朴仁淑)', '이만우(새누

In [ ]:
sug.iloc[8]

BILL_ID                         PRC_G1O5G0D4D1A5C1Z4P5V5P3L5R2P2U8
BILL_NO                                                    1914717
BILL_NAME                                            도로교통법 일부개정법률안
COMMITTEE                                                  안전행정위원회
PROPOSE_DT                                              2015-04-15
PROC_RESULT                                                 임기만료폐기
AGE                                                             19
DETAIL_LINK      http://likms.assembly.go.kr/bill/billDetail.do...
PROPOSER                                               민홍철의원 등 10인
MEMBER_LIST      http://likms.assembly.go.kr/bill/coactorListPo...
RST_PROPOSER                                                   민홍철
PUBL_PROPOSER                  박주선,부좌현,송영근,양승조,전정희,조경태,최원식,최재성,황인자
bill_content     제안이유 및 주요내용\n\n  유치원이나 어린이집, 체육시설, 학원 등의 어린이통학...
senators_list    민홍철(새정치민주연합/閔洪喆) 박주선(새정치민주연합/朴柱宣) 부좌현(새정치민주연합/...
Name: 28668, dtype: object

In [ ]:
sug.shape

(63, 14)

In [ ]:
###################### 수정 #################################
sug.to_csv('/content/data/suggest_1_percent.csv', index=False)

#2. Word embedding

##-1 데이터 불러오기 suggest ver4.0

In [ ]:
###################### 수정 #################################
df = pd.read_csv('/content/data/suggest_1_percent.csv')

In [ ]:
df.columns

Index(['BILL_ID', 'BILL_NO', 'BILL_NAME', 'COMMITTEE', 'PROPOSE_DT',
       'PROC_RESULT', 'AGE', 'DETAIL_LINK', 'PROPOSER', 'MEMBER_LIST',
       'RST_PROPOSER', 'PUBL_PROPOSER', 'bill_content', 'senators_list'],
      dtype='object')

In [ ]:
df.shape

(63, 14)

##word2vec 에 학습할 corpus생성하기

In [ ]:
from tqdm import tqdm

In [ ]:
from tqdm._tqdm_notebook import tqdm_notebook

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.*` instead of `tqdm._tqdm_notebook.*`
  """Entry point for launching an IPython kernel.


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 63 entries, 0 to 62
Data columns (total 14 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   BILL_ID        63 non-null     object
 1   BILL_NO        63 non-null     int64 
 2   BILL_NAME      63 non-null     object
 3   COMMITTEE      62 non-null     object
 4   PROPOSE_DT     63 non-null     object
 5   PROC_RESULT    63 non-null     object
 6   AGE            63 non-null     int64 
 7   DETAIL_LINK    63 non-null     object
 8   PROPOSER       63 non-null     object
 9   MEMBER_LIST    63 non-null     object
 10  RST_PROPOSER   63 non-null     object
 11  PUBL_PROPOSER  61 non-null     object
 12  bill_content   63 non-null     object
 13  senators_list  63 non-null     object
dtypes: int64(2), object(12)
memory usage: 7.0+ KB


In [ ]:
df.head()

BILL_ID  BILL_NO  \
0  PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3  1900574   
1                              026103   162692   
2                              036814   174918   
3  PRC_V0Y7Z0N4I1H0O0J9S4C6C3Q5B3U3F7   176375   
4                              034791   174238   

                        BILL_NAME  COMMITTEE  PROPOSE_DT PROC_RESULT  AGE  \
0  산업기술의 유출방지 및 보호에 관한 법률 일부개정법률안  산업통상자원위원회  2012-07-09          폐기   19   
1                       주세법중개정법률안    재정경제위원회  2003-09-30          폐기   16   
2                    하수도법 일부개정법률안    환경노동위원회  2006-09-14          폐기   17   
3        농업협동조합의구조개선에관한법률 일부개정법률안  농림해양수산위원회  2007-04-06      대안반영폐기   17   
4      맹견의 사육·관리 및 수입제한 등에 관한 법률안  농림해양수산위원회  2006-04-12      임기만료폐기   17   

                                         DETAIL_LINK     PROPOSER  \
0  http://likms.assembly.go.kr/bill/billDetail.do...  정희수의원 등 12인   
1  http://likms.assembly.go.kr/bill/billDetail.do...   김정부의원등 17인   
2  http://likms.assembly.go.kr/bill/billDetail.do...   박재완의원등 11인   
3  http://likms.assembly.go.kr/bill/billDetail.do...   김명주의원등 10인   
4  http://likms.assembly.go.kr/bill/billDetail.do...   이성권의원등 10인   

                                         MEMBER_LIST RST_PROPOSER  \
0  http://likms.assembly.go.kr/bill/coactorListPo...          정희수   
1  http://likms.assembly.go.kr/bill/coactorListPo...          김정부   
2  http://likms.assembly.go.kr/bill/coactorListPo...          박재완   
3  http://likms.assembly.go.kr/bill/coactorListPo...          김명주   
4  http://likms.assembly.go.kr/bill/coactorListPo...          이성권   

                                       PUBL_PROPOSER  \
0        고희선,권은희,박대동,박인숙,이만우,이명수,이현재,정우택,주영순,주호영,황영철   
1  강신성일,강인섭,권오을,김광원,박근혜,박상규,송광호,윤영탁,윤한도,이경재,이상배,임...   
2            공성진,김애실,배일도,신상진,심재철,엄호성,윤건영,이경재,이성구,이주호   
3                공성진,남경필,맹형규,신중식,원희룡,이명규,이성권,이인기,최구식   
4                권철현,김명주,김석준,김양수,김희정,박형준,서상기,이계경,정진석   

                                        bill_content  \
0  제안이유 및 주요내용\n\n  산업기밀보호센터에 따르면, 2005년 ～ 2011년간...   
1  ■ 제안이유\n  주류에 대한 주세 부과의 목적은 크게 재정수입 확보와 과도한 음주...   
2  ■ 제안이유 및 주요내용\n그동안 사실상 세금과 다름없이 강제 징수되어 국민들로부터...   
3  ■ 제안이유 \n시중 금융기관의 구조개선과는 달리, 농업협동조합중앙회는「농업협동조합...   
4  ■ 제안이유\n최근 도사견 등 맹견에 의한 인명피해가 빈번히 발생하여 심각한 사회문...   

                                       senators_list  
0  정희수(새누리당/鄭熙秀) 고희선(새누리당/高羲善) 권은희(새누리당/權恩嬉) 박대동(...  
1  김정부 강신성일 강인섭 권오을 김광원 박근혜 박상규 송광호 윤영탁 윤한도 이경재 이...  
2        박재완 공성진 김애실 배일도 신상진 심재철 엄호성 윤건영 이경재 이성구 이주호  
3            김명주 공성진 남경필 맹형규 신중식 원희룡 이명규 이성권 이인기 최구식  
4            이성권 권철현 김명주 김석준 김양수 김희정 박형준 서상기 이계경 정진석

In [ ]:
def tqdm_pandas(t):
  from pandas.core.frame import Series
  def inner(series, func, *args, **kwargs):
      t.total = series.size
      def wrapper(*args, **kwargs):
          t.update(1)
          return func(*args, **kwargs)
      result = series.apply(wrapper, *args, **kwargs)
      t.close()
      return result
  Series.progress_apply = inner

In [ ]:
df['tokenized'] = df['bill_content'].apply(tokenized_mecab)

In [ ]:
df['bill_content'].apply(tokenized_mecab)

0     제안 이유 및 주요 내용 산업 기밀 보호 센터 에 따르 면 , 2005 년 ～ 20...
1     ■ 제안 이유 주류 에 대한 주세 부과 의 목적 은 크 게 재정 수입 확보 와 과도...
2     ■ 제안 이유 및 주요 내용 그동안 사실 상 세금 과 다름없이 강제 징수 되 어 국...
3     ■ 제안 이유 시중 금융 기관 의 구조 개선 과 는 달리 , 농업 협동조합 중앙 회...
4     ■ 제안 이유 최근 도사견 등 맹견 에 의한 인명 피해 가 빈번히 발생 하 여 심각...
5     제안 이유 및 주요 내용 현행법 은 가축 전염병 에 걸렸 거나 걸렸 다고 믿 을 만...
6     제안 이유 및 주요 내용 현행법 은 중소기업 진흥 공단 의 사업 을 위하 여 적립 ...
7     제안 이유 현재 의료 사고 로 인한 피해 를 구제 받 기 위해서 는 「 의료법 」 ...
8     제안 이유 및 주요 내용 유치원 이나 어린이집 , 체육 시설 , 학원 등 의 어린이...
9     ■ 제안 이유 現行 法 은 알미늄 과 食器 , 법랑 製品 은 無稅 임 에 도 不拘 ...
10    제안 이유 롯데호텔 제주 , 롯데 쇼핑 , 농심 메가 마트 , 교보생명 , 대한 생...
11    제안 이유 및 주요 내용 현행법 상 교역 및 경제 분야 협력 사업 추진 중 대통령령...
12    제안 이유 및 주요 내용 여권 에 는 「 여권법 」 에 따라 성명 , 성별 , 주민...
13    제안 이유 및 주요 내용 현행법 은 안전 인증 및 자율 안전 확인 신고 등 의 표시...
14    ■ 제안 이유 및 주요 내용 현행법 제 16 조 의 3 에서 규정 하 고 있 는 6...
15    제안 이유 여야 가 적대 적 대립 속 에 국회 파행 으로 이어지 는 악순환 은 지난...
16    ■ 제안 이유 및 주요 내용 제안 이유 현행법 은 민간 시장 을 통한 일명 뉴스 테...
17    ■ 제안 이유 우리나라 의 합계 출산율 은 2002 년 1 . 17 을 거쳐

In [ ]:
df.head(3)

BILL_ID  BILL_NO  \
0  PRC_W1K2Y0J7S0D9T0C9O2G5Y0I9J1X0C3  1900574   
1                              026103   162692   
2                              036814   174918   

                        BILL_NAME  COMMITTEE  PROPOSE_DT PROC_RESULT  AGE  \
0  산업기술의 유출방지 및 보호에 관한 법률 일부개정법률안  산업통상자원위원회  2012-07-09          폐기   19   
1                       주세법중개정법률안    재정경제위원회  2003-09-30          폐기   16   
2                    하수도법 일부개정법률안    환경노동위원회  2006-09-14          폐기   17   

                                         DETAIL_LINK     PROPOSER  \
0  http://likms.assembly.go.kr/bill/billDetail.do...  정희수의원 등 12인   
1  http://likms.assembly.go.kr/bill/billDetail.do...   김정부의원등 17인   
2  http://likms.assembly.go.kr/bill/billDetail.do...   박재완의원등 11인   

                                         MEMBER_LIST RST_PROPOSER  \
0  http://likms.assembly.go.kr/bill/coactorListPo...          정희수   
1  http://likms.assembly.go.kr/bill/coactorListPo...          김정부   
2  http://likms.assembly.go.kr/bill/coactorListPo...          박재완   

                                       PUBL_PROPOSER  \
0        고희선,권은희,박대동,박인숙,이만우,이명수,이현재,정우택,주영순,주호영,황영철   
1  강신성일,강인섭,권오을,김광원,박근혜,박상규,송광호,윤영탁,윤한도,이경재,이상배,임...   
2            공성진,김애실,배일도,신상진,심재철,엄호성,윤건영,이경재,이성구,이주호   

                                        bill_content  \
0  제안이유 및 주요내용\n\n  산업기밀보호센터에 따르면, 2005년 ～ 2011년간...   
1  ■ 제안이유\n  주류에 대한 주세 부과의 목적은 크게 재정수입 확보와 과도한 음주...   
2  ■ 제안이유 및 주요내용\n그동안 사실상 세금과 다름없이 강제 징수되어 국민들로부터...   

                                       senators_list  \
0  정희수(새누리당/鄭熙秀) 고희선(새누리당/高羲善) 권은희(새누리당/權恩嬉) 박대동(...   
1  김정부 강신성일 강인섭 권오을 김광원 박근혜 박상규 송광호 윤영탁 윤한도 이경재 이...   
2        박재완 공성진 김애실 배일도 신상진 심재철 엄호성 윤건영 이경재 이성구 이주호   

                                           tokenized  
0  제안 이유 및 주요 내용 산업 기밀 보호 센터 에 따르 면 , 2005 년 ～ 20...  
1  ■ 제안 이유 주류 에 대한 주세 부과 의 목적 은 크 게 재정 수입 확보 와 과도...  
2  ■ 제안 이유 및 주요 내용 그동안 사실 상 세금 과 다름없이 강제 징수 되 어 국...

In [ ]:
#stop words 리스트에 저장
url= "/content/data/stopwords-ko.txt"    

stopwords_file = list(open(url,"r"))

list_stopword = []
for i in stopwords_file:
    list_stopword.append(i[:-1])
    

list_stopword.append('제안이유')
list_stopword.append('주요')
list_stopword.append('내용')
####추가####################################
list_stopword.append("'")
list_stopword.append('"')
list_stopword.append("■")
list_stopword.append("「")
list_stopword.append("」")

In [ ]:
len(list_stopword)

683

In [ ]:
#stropwords 제거
%%time
df['cleared'] = df['tokenized'].apply(lambda x: out_stopwords(x, list_stopwords = list_stopword))

data =  ['제안', '이유', '및', '주요', '내용', '산업', '기밀', '보호', '센터', '에', '따르', '면', ',', '2005', '년', '～', '2011', '년', '간', '국내', '첨단', '기술', '을', '해외', '로', '불법', '유출', '하', '였', '거나', '유출', '을', '기도', '한', '사건', '은', '총', '264', '건', '으로', '2005', '년', '29', '건', ',', '2006', '년', '31', '건', ',', '2007', '년', '32', '건', ',', '2008', '년', '42', '건', ',', '2009', '년', '43', '건', ',', '2010', '년', '41', '건', ',', '2011', '년', '46', '건', '으로', '매년', '꾸준히', '증가', '하', '고', '있', '는', '추세', '이', '며', ',', '국내', '기업', '간', '기술', '유출', '사건', '도', '1999', '년', '39', '건', '에서', '2009', '년', '에', '는', '648', '.', '7', '%', '증가', '한', '292', '건', '에', '달하', '고', '있', '음', '.', '현행법', '은', '국내', '핵심', '기술', '을', '보호', '하', '기', '위해', '산업', '기술', '의', '부정', '한', '해외', '유출', '등', '에', '대한', '처벌', '규정', '을', '두', '고', '있', '으나', ',', '산업', '스파이', '는', '증가', '추세', '이', '며', '이', '로', '인해', '개발자', '와', '관련', '기업', ',', '그리고', '국가', '적', '차원', '의', '손실', '도', '막대', '한', '수준', '에', '달하', '는', '실정', '임', '.', 

In [ ]:
df['cleared']

0     [제안, 이유, 산업, 기밀, 보호, 센터, 따르, 면, 2005, 2011, 간,...
1     [제안, 이유, 주류, 대한, 주세, 부과, 목적, 은, 크, 게, 재정, 수입, ...
2     [제안, 이유, 그동안, 사실, 상, 세금, 다름없이, 강제, 징수, 되, 국민, ...
3     [제안, 이유, 시중, 금융, 기관, 구조, 개선, 는, 달리, 농업, 협동조합, ...
4     [제안, 이유, 최근, 도사견, 맹견, 의한, 인명, 피해, 빈번히, 발생, 심각,...
5     [제안, 이유, 현행법, 은, 가축, 전염병, 걸렸, 거나, 걸렸, 다고, 믿, 만...
6     [제안, 이유, 현행법, 은, 중소기업, 진흥, 공단, 사업, 위하, 적립, 된, ...
7     [제안, 이유, 현재, 의료, 사고, 인한, 피해, 구제, 받, 기, 는, 의료법,...
8     [제안, 이유, 유치원, 이나, 어린이집, 체육, 시설, 학원, 어린이, 통학, 버...
9     [제안, 이유, 現行, 法, 은, 알미늄, 食器, 법랑, 製品, 은, 無稅, 임, ...
10    [제안, 이유, 롯데호텔, 제주, 롯데, 쇼핑, 농심, 메가, 마트, 교보생명, 대...
11    [제안, 이유, 현행법, 상, 교역, 경제, 분야, 협력, 사업, 추진, 중, 대통...
12    [제안, 이유, 여권, 는, 여권법, 성명, 성별, 주민, 등록, 번호, 개인, 식...
13    [제안, 이유, 현행법, 은, 안전, 인증, 자율, 안전, 확인, 신고, 표시, 없...
14    [제안, 이유, 현행법, 16, 조, 규정, 고, 있, 는, 25, 전몰군경, 자녀...
15    [제안, 이유, 여야, 적대, 적, 대립, 속, 국회, 파행, 이어지, 는, 악순환...
16    [제안, 이유, 제안, 이유, 현행법, 은, 민간, 시장, 통한, 일명, 뉴스, 테...
17    [제안, 이유, 우리나라, 합계, 출산율, 은, 2002, 17, 거쳐, 2

In [ ]:
len(df['cleared'].loc[0])

183

In [ ]:
type( df['cleared'].loc[0] )

list

In [ ]:
tokenized = ''
####수정####################################
for i in range(df['cleared'].shape[0]):
  line_one= df['cleared'].loc[i]
  #print("line_one = ", line_one)
  content = " ".join(line_one)
#법안당 100개의 토큰 가지도록 함
  for i in range(100) : 
    content = content.replace(str(i),"")

  #content = content.replace("1","")
  #print("contents =", contents)
  
  tokenized = tokenized + "{}\n".format(content)
  print(i, "tokenized =", tokenized)
  #print("="*100)
####수정####################################

f = open("corpus ver3.0 (전체, stopword 제거).txt", 'w')
f.write(tokenized)
f.close()

99 tokenized = 제안 이유 산업 기밀 보호 센터 따르 면   간 국내 첨단 기술 해외 불법 유출 였 거나 유출 기도 한 사건 은 총  건   건   건   건   건   건   건   건 매년 꾸준히 증가 고 있 는 추세 며 국내 기업 간 기술 유출 사건 도   건  는  증가 한  건 달하 고 있 음 현행법 은 국내 핵심 기술 보호 기 위해 산업 기술 부정 한 해외 유출 대한 처벌 규정 두 고 있 으나 산업 스파이 는 증가 추세 며 인해 개발자 관련 기업 국가 적 차원 손실 도 막대 한 수준 달하 는 실정 임 국내 산업 기술 부정 한 해외 유출 방지 기 위해 국내 첨단 기술 해외 불법 유출 한 는 현행법 상 처벌 이름 신상 정보 관련 범죄 요지 최대 간 공개 도록 국민 관련 범죄 심각 성 충분히 인지 시키 도록 고 국내 핵심 기술 해외 유출 따른 향후 국가 적 차원 막대 한 손실 피해 최소 화 려는 임 안  조 신설

99 tokenized = 제안 이유 산업 기밀 보호 센터 따르 면   간 국내 첨단 기술 해외 불법 유출 였 거나 유출 기도 한 사건 은 총  건   건   건   건   건   건   건   건 매년 꾸준히 증가 고 있 는 추세 며 국내 기업 간 기술 유출 사건 도   건  는  증가 한  건 달하 고 있 음 현행법 은 국내 핵심 기술 보호 기 위해 산업 기술 부정 한 해외 유출 대한 처벌 규정 두 고 있 으나 산업 스파이 는 증가 추세 며 인해 개발자 관련 기업 국가 적 차원 손실 도 막대 한 수준 달하 는 실정 임 국내 산업 기술 부정 한 해외 유출 방지 기 위해 국내 첨단 기술 해외 불법 유출 한 는 현행법 상 처벌 이름 신상 정보 관련 범죄 요지 최대 간 공개 도록 국민 관련 범죄 심각 성 충분히 인지 시키 도록 고 국내 핵심 기술 해외 유출 따른 향후 국가 적 차원 막대 한 손실 피해 최소 화 려는 임 안  조 신설
제안 이유 주류 대한 주세 부과 목적 은 크 게 재정 수입 확보 과도 한 음주 방지 통한 외부 불 경제 감

In [ ]:
direc ='corpus ver3.0 (전체, stopword 제거).txt'

In [ ]:
tokenized = ''
for content in df['cleared'].values:
    tokenized = tokenized + "{} \n".format(content)
    
f = open("corpus ver3.0 (전체, stopword 제거).txt", 'w')
f.write(tokenized)
f.close()

In [ ]:
#줄별 토큰화 단어를 리스트로 저장
for sent in open(direc).readlines():
  print("sent = ", sent)
  print("type(sent)=", type(sent))
  print("sent.strip().split(" ")=", sent.strip().split())
  print("="*100)

sent =  ['제안', '이유', '산업', '기밀', '보호', '센터', '따르', '면', '2005', '2011', '간', '국내', '첨단', '기술', '해외', '불법', '유출', '였', '거나', '유출', '기도', '한', '사건', '은', '총', '264', '건', '2005', '29', '건', '2006', '31', '건', '2007', '32', '건', '2008', '42', '건', '2009', '43', '건', '2010', '41', '건', '2011', '46', '건', '매년', '꾸준히', '증가', '고', '있', '는', '추세', '며', '국내', '기업', '간', '기술', '유출', '사건', '도', '1999', '39', '건', '2009', '는', '648', '증가', '한', '292', '건', '달하', '고', '있', '음', '현행법', '은', '국내', '핵심', '기술', '보호', '기', '위해', '산업', '기술', '부정', '한', '해외', '유출', '대한', '처벌', '규정', '두', '고', '있', '으나', '산업', '스파이', '는', '증가', '추세', '며', '인해', '개발자', '관련', '기업', '국가', '적', '차원', '손실', '도', '막대', '한', '수준', '달하', '는', '실정', '임', '국내', '산업', '기술', '부정', '한', '해외', '유출', '방지', '기', '위해', '국내', '첨단', '기술', '해외', '불법', '유출', '한', '는', '현행법', '상', '처벌', '이름', '신상', '정보', '관련', '범죄', '요지', '최대', '간', '공개', '도록', '국민', '관련', '범죄', '심각', '성', '충분히', '인지', '시키', '도록', '고', '국내', '핵심', '기술', '해외', '유출', '따른', '향후', 

In [ ]:
corpus = [sent.strip().split(" ") for sent in open(direc).readlines()]

In [ ]:
corpus

[["['제안',",
  "'이유',",
  "'산업',",
  "'기밀',",
  "'보호',",
  "'센터',",
  "'따르',",
  "'면',",
  "'2005',",
  "'2011',",
  "'간',",
  "'국내',",
  "'첨단',",
  "'기술',",
  "'해외',",
  "'불법',",
  "'유출',",
  "'였',",
  "'거나',",
  "'유출',",
  "'기도',",
  "'한',",
  "'사건',",
  "'은',",
  "'총',",
  "'264',",
  "'건',",
  "'2005',",
  "'29',",
  "'건',",
  "'2006',",
  "'31',",
  "'건',",
  "'2007',",
  "'32',",
  "'건',",
  "'2008',",
  "'42',",
  "'건',",
  "'2009',",
  "'43',",
  "'건',",
  "'2010',",
  "'41',",
  "'건',",
  "'2011',",
  "'46',",
  "'건',",
  "'매년',",
  "'꾸준히',",
  "'증가',",
  "'고',",
  "'있',",
  "'는',",
  "'추세',",
  "'며',",
  "'국내',",
  "'기업',",
  "'간',",
  "'기술',",
  "'유출',",
  "'사건',",
  "'도',",
  "'1999',",
  "'39',",
  "'건',",
  "'2009',",
  "'는',",
  "'648',",
  "'증가',",
  "'한',",
  "'292',",
  "'건',",
  "'달하',",
  "'고',",
  "'있',",
  "'음',",
  "'현행법',",
  "'은',",
  "'국내',",
  "'핵심',",
  "'기술',",
  "'보호',",
  "'기',",
  "'위해',",
  "'산업',",
  "'기술',",
  "'부정',",
  "'한',",
  "'해외',",
  "'유출',",
 

##-3 word2vec 학습하기 

In [ ]:
#모델 생성. 
 %%time
model_w2v = embedding_model = Word2Vec(corpus, size=100, window = 5, min_count=5,  
                           workers=12, iter=500, hs=0, sg=1)

CPU times: user 26.3 s, sys: 977 ms, total: 27.3 s
Wall time: 22 s


In [ ]:
model_w2v 

In [ ]:
# Word2Vec(corpus, size=100, window = 5, min_count=10,  
#                            workers=12, iter=500, hs=0, sg=1)

In [ ]:
model_w2v.save('/content/word2vec ver2.0 (iter500).model')

In [ ]:
model_test = Word2Vec.load('/content/word2vec ver2.0 (iter500).model')

In [ ]:
model_test

In [ ]:
####### 추가 #######################3
######## wordvector 가 만들어진 단어 리스트 (10번 이상 사용된 단어만 벡터가 만들어짐 min_count=10 )
model_test.wv.vocab.keys()

dict_keys(["['제안',", "'이유',", "'산업',", "'보호',", "'센터',", "'따르',", "'면',", "'간',", "'국내',", "'기술',", "'해외',", "'유출',", "'였',", "'거나',", "'한',", "'사건',", "'은',", "'건',", "'41',", "'매년',", "'증가',", "'고',", "'있',", "'는',", "'추세',", "'며',", "'기업',", "'도',", "'음',", "'현행법',", "'핵심',", "'기',", "'위해',", "'대한',", "'처벌',", "'규정',", "'두',", "'으나',", "'인해',", "'관련',", "'국가',", "'적',", "'손실',", "'수준',", "'실정',", "'임',", "'방지',", "'상',", "'정보',", "'도록',", "'국민',", "'성',", "'시키',", "'따른',", "'피해',", "'화',", "'려는',", "'안',", "'조',", "'신설']", "'주세',", "'부과',", "'목적',", "'게',", "'재정',", "'수입',", "'확보',", "'불',", "'경제',", "'감소',", "'수',", "'규모',", "'역할',", "'되',", "'나라',", "'제도',", "'중',", "'100',", "'결과',", "'율',", "'주',", "'현행',", "'체계',", "'인',", "'비해',", "'높',", "'된',", "'사회',", "'비용',", "'라는',", "'과세',", "'적용',", "'건전',", "'문화',", "'함',", "'건강',", "'소비자',", "'부담',", "'위하',", "'같',", "'인하',", "'분',", "'조정',", "'조제',", "'항',", "'호',", "'라',", "'사실',", "'강제',", "'징수',", "'받',", "'부담금',", "'효율',", "'불구'

In [ ]:
####추가 ####################################
for word in model_test.wv.vocab.keys():
  print("word = ", word)
  print("="*100)

word =  ['제안',
word =  '이유',
word =  '산업',
word =  '보호',
word =  '센터',
word =  '따르',
word =  '면',
word =  '간',
word =  '국내',
word =  '기술',
word =  '해외',
word =  '유출',
word =  '였',
word =  '거나',
word =  '한',
word =  '사건',
word =  '은',
word =  '건',
word =  '41',
word =  '매년',
word =  '증가',
word =  '고',
word =  '있',
word =  '는',
word =  '추세',
word =  '며',
word =  '기업',
word =  '도',
word =  '음',
word =  '현행법',
word =  '핵심',
word =  '기',
word =  '위해',
word =  '대한',
word =  '처벌',
word =  '규정',
word =  '두',
word =  '으나',
word =  '인해',
word =  '관련',
word =  '국가',
word =  '적',
word =  '손실',
word =  '수준',
word =  '실정',
word =  '임',
word =  '방지',
word =  '상',
word =  '정보',
word =  '도록',
word =  '국민',
word =  '성',
word =  '시키',
word =  '따른',
word =  '피해',
word =  '화',
word =  '려는',
word =  '안',
word =  '조',
word =  '신설']
word =  '주세',
word =  '부과',
word =  '목적',
word =  '게',
word =  '재정',
word =  '수입',
word =  '확보',
word =  '불',
word =  '경제',
word =  '감소',
word =  '수',
word =  '규모',
word =  '역할',


In [ ]:
#모델 불러와서 단어유사도 확인해보기
#비슷한 단어들끼리 유사하도록 단어 임베딩이 잘된 것을 확인할 수가 있다.
#model_test = Word2Vec.load('models/word2vec ver2.0 (iter500).model')
#model_test = Word2Vec.load('/content/word2vec ver2.0 (iter500).model')

In [ ]:
#######  
model_test.wv.most_similar("'자문',")

[("'인체',", 0.6153258085250854),
 ("'조직',", 0.5928031206130981),
 ("'심의',", 0.46765583753585815),
 ("'위원',", 0.4653356373310089),
 ("'구성',", 0.4466226100921631),
 ("'안전',", 0.42011770606040955),
 ("'원인',", 0.39623749256134033),
 ("'혈유',", 0.395083487033844),
 ("'보군',", 0.3869606852531433),
 ("'위원회',", 0.3570204973220825)]

In [ ]:
#display(Image('/content/images/강기윤.jpg'))

아래 코드를 사용하면 위 그림에서 어떤 단어들이 뭉쳐있는지 직접 확인해볼 수가 있다.
웹 기반이어서 jupyter notebook에는 저장이 되지 않는다.

#3법안 벡터 만들기 Sentence2vec

##-1 데이터, word2vec 모델 불러오기

In [ ]:
w2v_model = Word2Vec.load('/content/word2vec ver2.0 (iter500).model')

In [ ]:
bills = pd.read_csv("/content/data/suggest_1_percent.csv")

In [ ]:
bills.shape[0]

63

In [ ]:
#제20대 국회 입법 추출
bills_20 = bills[bills['AGE']==20]

In [ ]:
bills_20.shape[0]

24

In [ ]:
bills_20.to_csv('data/20th bills vector ver5.0 (word2vec).csv', index=False)

##-2 법안 벡터 만들기

In [ ]:
word_dict = {}
for vocab in tqdm(w2v_model.wv.index2word):
    word_dict[vocab] = w2v_model.wv[vocab]

100%|██████████| 565/565 [00:00<00:00, 60081.17it/s]


In [ ]:
%%time
bills_20['tokenized'] = bills_20['bill_content'].apply(tokenized_mecab)
bills_20['cleared'] = bills_20['tokenized'].apply(lambda x: out_stopwords(x, list_stopwords = list_stopword))
bills_20['cleared'] = [' '.join(map(str, l)) for l in bills_20['cleared']]

data =  ['제안', '이유', '및', '주요', '내용', '여권', '에', '는', '「', '여권법', '」', '에', '따라', '성명', ',', '성별', ',', '주민', '등록', '번호', '등', '개인', '을', '식별', '할', '수', '있', '는', '정보', '가', '수록', '되', '어', '있', '으며', ',', '이', '에', '따라', '현행', '「', '국민', '건강', '보험법', '」', '제', '12', '조', '는', '여권', '을', '국내', '신분증', '으로', '인정', '하', '고', '있', '음', '.', '그런데', ',', '여권', '은', '우리', '국민', '이', '타국', '에서', '숙박', '·', '교통', '등', '을', '이용', '할', '경우', '제시', '하', '는', '신분증', '인', '바', ',', '서비스', '의', '이용', '과정', '에서', '국민', '들', '의', '주민', '등록', '번호', '등', '신원', '관련', '정보', '가', '유출', '되', '기', '쉬운', '구조', '이', '며', '유출', '된', '정보', '가', '범죄', '에', '악용', '되', '어', '우리', '국민', '들', '이', '입', '은', '피해', '가', '증가', '하', '고', '있', '는', '상황', '임', '.', '따라서', '개인', '정보', '보호', '를', '위하', '여', '여권', '의', '수록', '정보', '에서', '주민', '등록', '번호', '를', '제외', '할', '필요', '가', '있', '어', '외교부', '는', '행안', '부', '와', '함께', '관련', '회의', '를', '통해', '2020', '년', '차세대', '전자', '여권', '도입', '과', '연계', '하', '여', '주민', '등록', '번호', '뒷자

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documen

In [ ]:
bills_20.columns

Index(['BILL_ID', 'BILL_NO', 'BILL_NAME', 'COMMITTEE', 'PROPOSE_DT',
       'PROC_RESULT', 'AGE', 'DETAIL_LINK', 'PROPOSER', 'MEMBER_LIST',
       'RST_PROPOSER', 'PUBL_PROPOSER', 'bill_content', 'senators_list',
       'tokenized', 'cleared'],
      dtype='object')

In [ ]:
%%time
dict_bills_vector = {}
for idx in tqdm(bills_20.index):
    print(idx)
    list_vector = []
#cleared 의 줄마다 단어로 split
    for word in bills_20.loc[idx]['cleared'].split():
#        print(word)
#word_dict에 있다면 단어의 벡터값을 list_vector에 넣는다
        if word in word_dict.keys():
            print("word_dict에 있네~")
            list_vector.append(word_dict[word])
        else :
            print("음습니다")

    dict_bills_vector[bills_20.loc[idx]['BILL_ID']] = np.sum(list_vector, axis=0).tolist()

KeyError: ignored

In [ ]:
%%time
dict_bills_vector = {}
for idx in tqdm(bills_20.index):
    list_vector = []
    for word in bills_20.loc[idx]['cleared'].split():
        if word in word_dict.keys():
            list_vector.append(word_dict[word])
    dict_bills_vector[bills_20.loc[idx]['BILL_ID']] = np.sum(list_vector, axis=0).tolist()

100%|██████████| 24/24 [00:00<00:00, 1064.30it/s]

CPU times: user 20.8 ms, sys: 1.98 ms, total: 22.8 ms
Wall time: 30.3 ms


In [ ]:
word_dict['신설']

KeyError: ignored

In [ ]:
bills_20['vector'] = bills_20['BILL_ID'].map(dict_bills_vector)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [ ]:
bills_20.to_csv('data/20th bills vector ver5.0 (word2vec).csv', index=False)

##-3 의원 벡터 만들기

In [ ]:
senators_20_list = []
similar_senators = bills_20['senators_list'].str.split(' ').str
list(similar_senators[3])

['김두관(더불어민주당/金斗官)',
 '위성곤(더불어민주당/魏聖坤)',
 '김무성(미래통합당/金武星)',
 '김병욱(더불어민주당/金炳旭)',
 '송석준(자유한국당/宋錫俊)',
 '김용태(자유한국당/金容兌)',
 '김세연(바른정당/金世淵)',
 '김정호(더불어민주당/金禎鎬)',
 '김성수(더불어민주당/金聖洙)',
 '김삼화(바른미래당/金三和)',
 '박선숙(국민의당/朴仙淑)',
 '박성중(바른정당/朴成重)',
 '송언석(자유한국당/宋彦錫)',
 '박주민(더불어민주당/朴柱民)',
 '김상훈(자유한국당/金相勳)',
 '민홍철(더불어민주당/閔洪喆)',
 '김수민(국민의당/金秀玟)',
 '김영호(더불어민주당/金映豪)',
 '이용주(민주평화당/李勇周)',
 '김관영(국민의당/金寬永)',
 '김성원(새누리당/金成願)',
 '김석기(자유한국당/金碩基)',
 '김현권(더불어민주당/金玄權)',
 '김기선(자유한국당/金起善)']

In [ ]:
for i in list(similar_senators[i]):
  list_vector = []
  list_vector.append(i)

In [ ]:
bills_20.columns

Index(['BILL_ID', 'BILL_NO', 'BILL_NAME', 'COMMITTEE', 'PROPOSE_DT',
       'PROC_RESULT', 'AGE', 'DETAIL_LINK', 'PROPOSER', 'MEMBER_LIST',
       'RST_PROPOSER', 'PUBL_PROPOSER', 'bill_content', 'senators_list',
       'tokenized', 'cleared', 'vector'],
      dtype='object')

In [ ]:
senator_name = []
party_name = []
for idx in tqdm(bills_20.index):
#    print(idx)    
#cleared 의 줄마다 단어로 spli
    for word in bills_20.loc[idx]['senators_list'].split():
        party = word.split('/')[0]
        word = word.split('/')[1]
        if len(word) > 3:
          word = word[0:3]
          party = party[4:]
        else : 
            word = word[0:2]
            party = party[3:]
                         
#법안에 있는 단어이면 단어의 벡터값을 list_vector에 더한다
        senator_name.append(word)
        party_name.append(party)

senator_20 = pd.DataFrame(senator_name)
senator_20['NAME_HAN'] = pd.DataFrame(senator_name)
senator_20['PARTY'] = pd.DataFrame(party_name)


100%|██████████| 24/24 [00:00<00:00, 3441.83it/s]


In [ ]:
senator_20

0 NAME_HAN   PARTY
0    沈載權      沈載權  더불어민주당
1    姜炳遠      姜炳遠  더불어민주당
2    姜昌一      姜昌一  더불어민주당
3    金斗官      金斗官  더불어민주당
4    金炳旭      金炳旭  더불어민주당
..   ...      ...     ...
298  柳在仲      柳在仲   자유한국당
299  李喆圭      李喆圭   자유한국당
300  鄭甲潤      鄭甲潤   자유한국당
301  趙慶泰      趙慶泰   자유한국당
302  秋慶鎬      秋慶鎬   자유한국당

[303 rows x 3 columns]

In [ ]:
%%time
dict_senator_vector_20 = {}
for idx in tqdm(senator_20.index):
    korean_name = senator_20['NAME_HAN'].loc[idx]
    chinese_name = senator_20['NAME_HAN'].loc[idx]

    participated_bills = list(bills_20[bills_20['senators_list'].str.contains(chinese_name)]['BILL_ID'].values)
    
    bill_vector_list = []
    for bill_id in participated_bills:
        bill_vector_list.append(np.array([float(i) for i in bills_20[bills_20['BILL_ID']==bill_id]['vector'].iloc[0][1:-1].split(', ')]))
    dict_senator_vector_20[chinese_name] = (np.sum(bill_vector_list, axis=0)/len(bill_vector_list)).tolist()
   

100%|██████████| 303/303 [00:00<00:00, 1126.34it/s]


IndexError: ignored

In [ ]:
senator_20_vector_party = senator_20.copy()

In [ ]:
senator_20_vector_party['vector'] = senator_20_vector_party['NAME_HAN'].map(dict_senator_vector_20)

In [ ]:
senator_20_vector_party

0 NAME_HAN   PARTY  vector
0    沈載權      沈載權  더불어민주당     NaN
1    姜炳遠      姜炳遠  더불어민주당     NaN
2    姜昌一      姜昌一  더불어민주당     NaN
3    金斗官      金斗官  더불어민주당     NaN
4    金炳旭      金炳旭  더불어민주당     NaN
..   ...      ...     ...     ...
298  柳在仲      柳在仲   자유한국당     NaN
299  李喆圭      李喆圭   자유한국당     NaN
300  鄭甲潤      鄭甲潤   자유한국당     NaN
301  趙慶泰      趙慶泰   자유한국당     NaN
302  秋慶鎬      秋慶鎬   자유한국당     NaN

[303 rows x 4 columns]

#4 국회의원 벡터 시각화

In [ ]:
from sklearn.manifold import TSNE
tsne = TSNE(n_components=2)

In [ ]:
vector_20 = pd.read_csv('data/senator_20 vector only vector ver5.0 (word2vec).csv')

FileNotFoundError: ignored

In [ ]:
vector_20

In [ ]:
senator_tsne = tsne.fit_transform(vector_20.iloc[:,1:-1])

In [ ]:
df_senator_20 = pd.DataFrame(senator_tsne, index=vector_20['index'].tolist(), columns=['x', 'y']).reset_index()
df_senator_20 = df_senator_20.merge(senator_20_vector_party[['NAME_HAN','PARTY']], left_on='index', right_on='NAME_HAN', how='left').drop(columns='NAME_HAN')
df_senator_20.to_excel("data/T-sne 20th ver5.0 (word2vec).xlsx", index=False)

In [ ]:
df_senator_20

In [ ]:
fig, ax = plt.subplots(figsize=(11.7, 8.27))
sns.scatterplot(ax=ax, data=df_senator_20, x="x", y="y", hue='PARTY')

In [ ]:
fig, ax = plt.subplots(figsize=(11.7, 8.27))
sns.scatterplot(ax=ax, data=df_senator_20, x="x", y="y", hue='PARTY')

#5. 국회의원 클러스터링 & 워드클라우드

##-1 클러스터 갯수 지정하기기

In [ ]:
# Hierarchical clustering 예시2 (실제 data로 응용하는 법)
import scipy.cluster.hierarchy as shc
data = snt_20_tsne.iloc[:, 1:3].values    # iloc 의미, 전체 row와 3~4번째 column의 값을 nparray 형식으로 반환

plt.figure(figsize=(10, 7))
plt.title("Senators Dendograms")
dend = shc.dendrogram(shc.linkage(data, method='ward'))    # dendrogram에서 적정 군집 수를 파악하고

In [ ]:
# Silhouette 분석 에시
range_n_clusters = range(9,15)

for n_clusters in range_n_clusters:
    clusterer = KMeans(n_clusters=n_clusters)
    preds = clusterer.fit_predict(snt_20_tsne[['x','y']])
    centers = clusterer.cluster_centers_

    score = silhouette_score(snt_20_tsne[['x','y']], preds)
    print("For n_clusters = {}, silhouette score is {}".format(n_clusters, round(score, 4)))

##-2 클러스터링

In [ ]:
model = KMeans(n_clusters=11)

model.fit(snt_20_tsne[['x','y']])

y_predict = model.fit_predict(snt_20_tsne[['x','y']])

In [ ]:
snt_20_tsne['cluster'] = y_predict

display(Image('./images/cluster11.png'))
이미지로 표시하는 법?

##-3 클러스터별 관심법안 word cloud

In [ ]:
for num in list(range(0,snt_20_tsne['cluster'].nunique())):
    cluster_num = num
    print("cluster",cluster_num,"시작","*"*50 )

    # cluster 내 발의 법안들 모아주기
    list_collect_ids = []
    print()
    for senator in snt_20[snt_20['cluster']==cluster_num]['index'].tolist():
        list_collect_ids.extend(bills_20_notnull[bills_20_notnull['senators_list'].str.contains(senator)]['BILL_ID'].values)
    print("cluster 내 발의법안 수: ", len(set(list_collect_ids)), '국회의원 수', len(snt_20[snt_20['cluster']==cluster_num]))

    # 공통 발의법안들 모아주기
    word_bags_cluster = ''
    for i in Counter(list_collect_ids).most_common(round(len(set(list_collect_ids))/20)):
        corpus = bills_20[bills_20['BILL_ID']==i[0]]['cleared'].iloc[0]
        word_bags_cluster = word_bags_cluster + corpus

    # wordcloud 만들기
    wc = WordCloud(background_color = "ivory",
                   font_path = "/Library/Fonts/NanumSquareRegular.ttf",
                   colormap = "Reds",
                   collocations = True, 
                   stopwords = stopwords_,
                   mask = mask_array)

    # WordCloud 출력하기
    wc.generate(word_bags_cluster)
    wc.to_image()

    # wordcloud 저장하기
    wc.to_file('data/images/[cluster11] cluster_{} ver1.0 5%.png'.format(cluster_num))

In [ ]:
cluster_num = 4

# cluster 내 발의 법안들 모아주기
list_collect_ids = []
for senator in snt_20[snt_20['cluster']==cluster_num]['index'].tolist():
    list_collect_ids.extend(bills_20_notnull[bills_20_notnull['senators_list'].str.contains(senator)]['BILL_ID'].values)

# 공통 발의법안들 모아주기
word_bags_cluster = ''
for i in Counter(list_collect_ids).most_common(round(len(set(list_collect_ids))/20)):
    corpus = bills_20[bills_20['BILL_ID']==i[0]]['cleared'].iloc[0]
    word_bags_cluster = word_bags_cluster + corpus

# wordcloud 만들기
wc = WordCloud(background_color = "ivory",
               font_path = "/Library/Fonts/NanumSquareRegular.ttf",
               colormap = "Reds",
               collocations = True, 
               stopwords = stopwords_,
               mask = mask_array)

# WordCloud 출력하기
wc.generate(word_bags_cluster)
wc.to_image()

워드 클라우드 출력 확인인

In [ ]:
cluster_num = 5

# cluster 내 발의 법안들 모아주기
list_collect_ids = []
for senator in snt_20[snt_20['cluster']==cluster_num]['index'].tolist():
    list_collect_ids.extend(bills_20_notnull[bills_20_notnull['senators_list'].str.contains(senator)]['BILL_ID'].values)

# 공통 발의법안들 모아주기
word_bags_cluster = ''
for i in Counter(list_collect_ids).most_common(round(len(set(list_collect_ids))/20)):
    corpus = bills_20[bills_20['BILL_ID']==i[0]]['cleared'].iloc[0]
    word_bags_cluster = word_bags_cluster + corpus

# wordcloud 만들기
wc = WordCloud(background_color = "ivory",
               font_path = "/Library/Fonts/NanumSquareRegular.ttf",
               colormap = "Reds",
               collocations = True, 
               stopwords = stopwords_,
               mask = mask_array)

# WordCloud 출력하기
wc.generate(word_bags_cluster)
wc.to_image()

#6 추천예시


In [ ]:
user_input='저는 장애인 아이를 자녀로 두고 있습니다. 차별금지법을 지지하며 장애인 복지서비스, 특수교육, 인권에 대해서 관심이 많습니다.'
user_vector = input2vec(user_input, list_stopword, word_dict)

In [ ]:
similar_senators(user_vector, snt)

In [ ]:
on_2D(user_vector,list(similar_senators(user_vector, snt)))

In [ ]:
dict_senators_bills = similar_bills(user_vector, bills_notnull, snt, word_dict, list(similar_senators(user_vector, snt)))
show_results(pd.DataFrame(show_bills(dict_senators_bills, bills_notnull, snt)))